In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from tf.app import use

In [3]:
A = use("ETCBC/bhsa:clone", checkout="clone")

**Locating corpus resources ...**

Before we start, we make a test instruction set.

We pick up all words whose lexeme starts with `BJT_` and that have multiple occurrence forms.
We collect the occurrence forms and use them to populate a spreadsheet with instructions.

See the file `ner/sheets/places.xlsx`

In [4]:
F = A.api.F

In [5]:
candidates = {}
candidates_utf8 = {}

for w in F.otype.s("word"):
    lex = F.lex.v(w)
    if not lex.startswith("BJT_"):
        continue
    lex_utf8 = F.lex_utf8.v(w)
    candidates.setdefault(lex, set()).add(F.g_cons.v(w))
    candidates_utf8.setdefault(lex_utf8, set()).add(F.g_cons_utf8.v(w))

multiples = {lex: shapes for (lex, shapes) in candidates.items() if len(shapes) > 1}
multiples_utf8 = {lex: shapes for (lex, shapes) in candidates_utf8.items() if len(shapes) > 1}

def show(d):
    for (k, vs) in sorted(d.items()):
        print(k)
        print("\t" + (" ; ".join(v.replace(" ", "_") for v in vs)))
        
show(multiples)
show(multiples_utf8)

BJT_C>N/
	BJT_C>N ; BJT_CN
BJT_DGWN/
	BJT_DGN ; BJT_DGWN
BJT_HJCMWT/
	BJT_HJCJMT ; BJT_HJCMT ; BJT_HJCMWT
BJT_XWRWN/
	BJT_XRWN ; BJT_XWRN ; BJT_XRN ; BJT_XWRWN
בית דגון
	בית_דגון ; בית_דגן
בית הישׁמות
	בית_הישׁמות ; בית_הישׁימת ; בית_הישׁמת
בית חורון
	בית_חורון ; בית_חורן ; בית_חרן ; בית_חרון
בית שׁאן
	בית_שׁאן ; בית_שׁן


Now we start with the entity assignment.

In [6]:
NE = A.makeNer()

In [8]:
NE.readInstructions("places", force=True)

4 entities with 11 occurrence specs
0 entities do not have occurrence specifiers
All occurrence specifiers are unambiguous


In [9]:
NE.makeInventory()
NE.showInventory()

בית.דגון                 LOC   בית_דגון                 1 x בית דגון
בית.דגון                 LOC   בית_דגן                  1 x בית דגון
בית.חורון                LOC   בית_חורון                5 x בית חורון
בית.חורון                LOC   בית_חורן                 5 x בית חורון
בית.חורון                LOC   בית_חרון                 3 x בית חורון
בית.חורון                LOC   בית_חרן                  1 x בית חורון
Total 16


In [10]:
NE.setSet("power")

Annotation set power has 16 annotations


In [11]:
NE.resetSet()

Annotation set power has 0 annotations


In [12]:
NE.markEntities()

Already present:     0 x
Added:              16 x


In [14]:
results = NE.filterContent(anyEnt=True, showStats=None)

15 verses


In [15]:
NE.showContent(results)